# Exponential smoothing in Python

In [ ]:
from pandas import DataFrame
import matplotlib.pyplot as plt
from data201 import db_connection

%matplotlib inline

In [ ]:
conn = db_connection(config_file='stock-prices.ini')
cursor = conn.cursor()

In [ ]:
table = cursor.execute('SELECT * FROM recent_prices')
table = cursor.fetchall()
table

In [ ]:
def compute_exponential_smoothing(table, alpha):
    """
    @table the table of days, prices, and averages
    @alpha the alpha for exponential smoothing
    """
    smoothed = None
    
    for i in range(len(table)):
        price = table[i][1]
        smoothed = (alpha*price
                 + (1 - alpha)*(price if smoothed is None else smoothed))
        table[i] += (smoothed,)

    return table

In [ ]:
for alpha in [0.5, 0.2]:
    table = compute_exponential_smoothing(table, alpha)

table

In [ ]:
columns = ['days ago', 'price']

for alpha in [0.5, 0.2]:
    label = f'{alpha = }'
    columns += [label,]

df = DataFrame(table)
df.columns = columns
df

In [ ]:
plt.figure(figsize=(15, 10))

alphas = [0.5, 0.2]
first = True

for i in range(len(alphas)):
    alpha = alphas[i]
    graph_label = f'{alpha = }'

    rows = df.values.tolist()
    xs   = [row[0] for row in rows]
    ys   = [row[1] for row in rows]
    exps = [row[i + 2] for row in rows]
    
    # Initialize the graph.
    if first:
        plt.xticks(xs)
        plt.plot(xs, ys, linewidth=5)
        plt.title('Exponentially Smoothed Stock Prices')
        plt.xlabel('Days ago')
        plt.ylabel('Price')
        first = False

    # Plot the moving average line.
    plt.plot(xs, exps, label=graph_label)
    
plt.legend()
plt.show()

In [ ]:
conn.close()